# STFT Dataset Generation

In [1]:
import time
import os
import pprint
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import IPython.display as ipd
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import librosa
import librosa.display
import utils

In [2]:
AUDIO_DIR = os.environ.get('AUDIO_DIR')
print("audio directory: ",AUDIO_DIR)
print("Loading tracks.csv...")
tracks = utils.load('data/fma_metadata/tracks.csv')
#get only the small subset of the dataset
small = tracks[tracks['set', 'subset'] <= 'small']
print("small dataset shape:",small.shape)

audio directory:  ./data/fma_small/
Loading tracks.csv...
small dataset shape: (8000, 52)


In [3]:
#split into train, validation and test sets
train = small.index[small['set', 'split'] == 'training']
val = small.index[small['set', 'split'] == 'validation']
test = small.index[small['set', 'split'] == 'test']

print('{} training examples, {} validation examples, {} testing examples'.format(*map(len, [train, val, test])))


6400 training examples, 800 validation examples, 800 testing examples


In [4]:
genres=utils.load('data/fma_metadata/genres.csv')
#list of genres
genres_list=genres['title'].unique()

In [5]:
def expand_labels(labels_set):
    lbl_array = labels_set

    # Repeat each element 10 times using np.repeat()
    expanded_array = np.repeat(lbl_array, 10)

    # Create a new Categorical object from the expanded array
    expanded_categorical = pd.Categorical(expanded_array)

    # Print the expanded categorical variable
    return expanded_categorical

In [6]:
#retrieve labels for each subset
tr_labels = small.loc[small[('set', 'split')] == 'training', ('track', 'genre_top')].values
vl_labels = small.loc[small[('set', 'split')] == 'validation', ('track', 'genre_top')].values
ts_labels = small.loc[small[('set', 'split')] == 'test', ('track', 'genre_top')].values

tr_labels=expand_labels(tr_labels)
vl_labels=expand_labels(vl_labels)
ts_labels=expand_labels(ts_labels)


print('{} training labels, {} validation labels, {} testing labels'.format(*map(len, [tr_labels, vl_labels, ts_labels])))


64000 training labels, 8000 validation labels, 8000 testing labels


## Generate the STFT small dataset

### Let's get all the STFT spectrograms for each track audio in the dataset

Some tracks (6) of the original small dataset are corrupted or very small (1-2 seconds), these track has been replaced
by a script with other good tracks of the same genre from the dataset.

#### Important
Create a directory 'fma_small_stft' with 3 directories inside:
- 'train'
- 'validation'
- 'test'

In [ ]:
def generate_stft_files(dataset,directory):
    print("Generating files in the folder:",directory,"...")

    track_ids = np.array(dataset)
    
    error_list = [] #list of tracks which caused errors
    progress_bar = 1
    for track_id in track_ids:
        print("track id: ",track_id)

        try:
            #get the filename using the utils
            filename = utils.get_audio_path(AUDIO_DIR, track_id)
            print('File: {}'.format(filename))

            x, sr = librosa.load(filename, sr=None, mono=True) #load the MONO audio file from the data/fma_small directory
            #print('Duration: {:.2f}s, {} samples, sampling rate: {}'.format(x.shape[-1] / sr, x.size, sr))

            #calculate stft on each 3s clip of the 30s song
            for i in range (0,28,3):
                start, end = i, i+3 #start and end point of the clip
                #print("start: {}, end: {}".format(start,end))
                clip = x[start*sr:end*sr] #extract the clip
                #print("samples per clip:",len(clip),"duration in seconds = ",len(clip)/sr)
                #calculate stft using a window of 1024 sample and a hop length of 1024 sample
                stft = librosa.stft(clip, n_fft=1024, hop_length=1024)
                #take only the absolute value of the stft
                stft = np.abs(stft)
                #print("stft shape: {}".format(stft.shape))
                #transpose the stft
                stft = stft.T
                #print("stft shape (after transpose): {}".format(stft.shape))

                #resize the spectrogram to become 128x513 (adds padding with zeros if too short)
                stft = librosa.util.fix_length(stft, size=128, axis=0)[:, :513]

                #stft = stft[:128]
                print("stft shape (after fixing length to 128 frames): {}".format(stft.shape))

                save_filename = './data/fma_small_stft_transposed/' + directory + "/" +  str(track_id) + "_" + str(i//3)
                #print("Saving the stft vector in file:",save_filename) 
                np.save(save_filename,stft)
                #print("shape of the stft vector (clip " + str(i//3) + "): ", stft.shape)
                
        except Exception as e: #skip the songs which give error (file corrupted or song too short)
            print("ERROR on file: ",filename,"\nError information:", e)
            error_list.append(filename)
            
        print("Progress:" + str(progress_bar) + "/" + str(len(track_ids)))
        progress_bar +=1
        if(len(error_list)>0):
            print("***ERROR: {} tracks caused errors: {}".format(len(error_list),error_list))
        else:
            print("Procedure completed without errors.")
            
    print("\n\n###Procedure completed with {} errors: {}".format(len(error_list),error_list))


In [10]:
generate_stft_files(train,'train')

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:3/6400
Procedure completed without errors.
track id:  140
File: ./data/fma_small/000/000140.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:15/6400
Procedure completed without errors.
track id:  212
File: ./data/fma_small/000/000212.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shap

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:28/6400
Procedure completed without errors.
track id:  625
File: ./data/fma_small/000/000625.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shap

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:40/6400
Procedure completed without errors.
track id:  821
File: ./data/fma_small/000/000821.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shap

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:52/6400
Procedure completed without errors.
track id:  1102
File: ./data/fma_small/001/001102.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft sha

...

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:6346/6400
Procedure completed without errors.
track id:  149488
File: ./data/fma_small/149/149488.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:6358/6400
Procedure completed without errors.
track id:  149776
File: ./data/fma_small/149/149776.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft

Progress:6370/6400
Procedure completed without errors.
track id:  150080
File: ./data/fma_small/150/150080.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:6371/6400
Procedure completed without errors.
track id:  150265
File: ./data/fma_small/150/150265.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape 

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:6384/6400
Procedure completed without errors.
track id:  152425
File: ./data/fma_small/152/152425.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:6397/6400
Procedure completed without errors.
track id:  154413
File: ./data/fma_small/154/154413.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft

In [11]:
generate_stft_files(val,'validation')

Generating files in the folder: validation ...
track id:  148
File: ./data/fma_small/000/000148.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:1/800
Procedure completed without errors.
track id:  459
File: ./data/fma_small/000/000459.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing leng

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:13/800
Procedure completed without errors.
track id:  5191
File: ./data/fma_small/005/005191.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shap

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:25/800
Procedure completed without errors.
track id:  6463
File: ./data/fma_small/006/006463.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shap

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:37/800
Procedure completed without errors.
track id:  9560
File: ./data/fma_small/009/009560.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shap

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:49/800
Procedure completed without errors.
track id:  14318
File: ./data/fma_small/014/014318.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft sha

...

Progress:748/800
Procedure completed without errors.
track id:  142096
File: ./data/fma_small/142/142096.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:749/800
Procedure completed without errors.
track id:  142097
File: ./data/fma_small/142/142097.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (aft

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:761/800
Procedure completed without errors.
track id:  143296
File: ./data/fma_small/143/143296.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:773/800
Procedure completed without errors.
track id:  144600
File: ./data/fma_small/144/144600.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:785/800
Procedure completed without errors.
track id:  148211
File: ./data/fma_small/148/148211.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:797/800
Procedure completed without errors.
track id:  148303
File: ./data/fma_small/148/148303.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s

In [ ]:
generate_stft_files(test,'test')

Generating files in the folder: test ...
track id:  182
File: ./data/fma_small/000/000182.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:1/800
Procedure completed without errors.
track id:  704
File: ./data/fma_small/000/000704.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:13/800
Procedure completed without errors.
track id:  1249
File: ./data/fma_small/001/001249.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shap

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:25/800
Procedure completed without errors.
track id:  7383
File: ./data/fma_small/007/007383.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shap

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:37/800
Procedure completed without errors.
track id:  10385
File: ./data/fma_small/010/010385.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft sha

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:49/800
Procedure completed without errors.
track id:  10447
File: ./data/fma_small/010/010447.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft sha

...

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:703/800
Procedure completed without errors.
track id:  138022
File: ./data/fma_small/138/138022.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:715/800
Procedure completed without errors.
track id:  140620
File: ./data/fma_small/140/140620.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:727/800
Procedure completed without errors.
track id:  141616
File: ./data/fma_small/141/141616.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:739/800
Procedure completed without errors.
track id:  142534
File: ./data/fma_small/142/142534.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s

stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
Progress:751/800
Procedure completed without errors.
track id:  145067
File: ./data/fma_small/145/145067.mp3
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft shape (after fixing length to 128 frames): (128, 513)
stft s